# rollups_blobs_economics

> This notebook explores the economics of rollups and blobs from cryo transactions and blocks dataset.

In [1]:
# |default_exp rollups_blobs

In [16]:
# | export
from ethereum_block_explorer.cryo_query import cryoTransform

import os
import polars as pl
import re
import pprint
import jupyter_black

pl.Config.set_fmt_str_lengths(200)
pl.Config.set_fmt_float("full")
jupyter_black.load()

In [3]:
cd ../

/home/evan/Documents/ethereum_block_explorer


### Setup & Methodology
We label the sequencer submitter addresses from each L2 and analyze how much gas they consume in blocks. We measure the block utilization behavior of L2s pre EIP-4844 and then extrapolate, from historical demand, how saturated the initial data blob market will be. We focus on L1 gas usage instead of L2 TPS so that we can analyze gas costs independent to L2 data compression improvements.

* Gas is shown in gwei and calldata is shown in KB.

In [4]:
ct = cryoTransform()

In [5]:
directory_a: str = "data/raw/transactions"
directory_b: str = "data/raw/blocks"

synced_files: dict[str] = ct.sync_filenames(directory_a=directory_a, directory_b=directory_b)

In [9]:
# Sequencer Tags
# https://dune.com/queries/3302607
sequencers_l2: dict[str] = {
    "sequencer_addresses": [
        "0xc1b634853cb333d3ad8663715b08f41a3aec47cc",
        "0x6887246668a3b87f54deb3b94ba47a6f63f32985",
        "0x9228624c3185fcbcf24c1c9db76d8bef5f5dad64",
        "0x6667961f5e9c98a76a48767522150889703ed77d",
        "0xcf2898225ed05be911d3709d9417e86e0b4cfc8f",
        "0x148ee7daf16574cd020afa34cc658f8f3fbd2800",
        "0x16d5783a96ab20c9157d7933ac236646b29589a4",
        "0x5050f69a9786f081509234f1a7f4684b5e5b76c9",
    ],
    "sequencer_names": [
        "arbitrum",
        "optimism",
        "linea",
        "mantle",
        "scroll",
        "polygon_zkevm",
        "starknet",
        "base",
    ],
}

sequencer_labels_lf: pl.LazyFrame = pl.from_dict(sequencers_l2).lazy()

In [15]:
# Check if the lists have the same length
if len(synced_files[directory_a]) == len(synced_files[directory_b]):
    # Assuming both lists in synced_files have the same length
    for i in range(len(synced_files[directory_a])):
        # load LazyFrames
        txs_file: str = directory_a + "/" + synced_files[directory_a][i]
        blocks_file: str = directory_b + "/" + synced_files[directory_b][i]

        txs_lf: pl.LazyFrame = pl.scan_parquet(txs_file)
        blocks_lf: pl.LazyFrame = pl.scan_parquet(blocks_file)

        # combine and save
        tx_blocks_lf: pl.LazyFrame = (
            ct.extend_txs_blocks(txs_lf, blocks_lf)
            .join(
                sequencer_labels_lf,
                left_on="from_address",
                right_on="sequencer_addresses",
                how="left",
            )
            .drop("timestamp", "block_number_right")
            .filter(pl.col("sequencer_names").is_in(sequencers_l2["sequencer_names"]))
        )

        # make a new directory to save the files
        new_directory = "data/rollups"
        if not os.path.exists(new_directory):
            os.makedirs(new_directory)

        block_range_match: str = re.search(r"__(\d+_to_\d+)", txs_file)
        block_range = block_range_match.group(1)
        new_filename = f"{block_range}.parquet"

        tx_blocks_lf.collect(streaming=True).write_parquet(
            new_directory + "/" + new_filename
        )

else:
    print("The synced file lists for the two directories are not of the same length.")

KeyboardInterrupt: 

In [21]:
df_test = pl.read_parquet("data/rollups/*.parquet")

In [6]:
STOP

NameError: name 'STOP' is not defined

In [ ]:


# TODO - 
# cryo txs
txs_lf = pl.scan_parquet("data/raw/transactions/*.parquet")

# cryo blocks
blocks_lf = pl.scan_parquet("data/raw/blocks/*.parquet").select(
    "author", "block_number", "timestamp", "gas_used", "base_fee_per_gas"
)

# final df
tx_blocks_lf: pl.LazyFrame = (
    ct.extend_txs_blocks(txs_lf, blocks_lf)
    .join(
        sequencer_labels_lf,
        left_on="from_address",
        right_on="sequencer_addresses",
        how="left",
    )
    .drop("timestamp", "block_number_right")
    .filter(pl.col("sequencer_names").is_in(sequencers_l2["sequencer_names"]))
)

In [ ]:
batch_tx.collect(streaming=True)

In [ ]:
STOP

In [ ]:
# tx_blocks_lf.sink_parquet("data/rollup_blob.parquet")

In [ ]:
explore_df = pl.read_parquet("data/rollup_blob.parquet")

In [ ]:
# cryo txs
dataset_info = (
    (explore_df.select("block_number", "block_datetime"))
    .unique()
    .sort(by="block_number")
)

print(
    f"block range: {dataset_info['block_number'][0]} to {dataset_info['block_number'][-1]} = {dataset_info['block_number'][-1] - dataset_info['block_number'][0]} range"
)
pprint.pprint(dataset_info["block_number"].len())
print(
    f"block range: {dataset_info['block_datetime'][0]} to {dataset_info['block_datetime'][-1]}"
)

block range: 18030002 to 18254999 = 224997 range
127425
block range: 2023-08-30 21:10:23 to 2023-10-01 10:09:47


In [ ]:
pprint.pprint(explore_df.shape)
print(
    f"block range: {dataset_info['block_number'][-1]- dataset_info['block_number'][0]}"
)
pprint.pprint(explore_df["block_number"].unique().len())
pprint.pprint(explore_df.schema)

(292045, 30)
block range: 224997
127425
OrderedDict([('block_number', UInt32),
             ('transaction_index', UInt64),
             ('transaction_hash', String),
             ('nonce', UInt64),
             ('from_address', String),
             ('to_address', String),
             ('gas_limit', UInt64),
             ('gas_used', UInt64),
             ('transaction_type', UInt32),
             ('success', Boolean),
             ('n_input_bytes', UInt32),
             ('n_input_zero_bytes', UInt32),
             ('n_input_nonzero_bytes', UInt32),
             ('n_rlp_bytes', UInt32),
             ('chain_id', UInt64),
             ('author', String),
             ('gas_used_block', UInt64),
             ('transaction_index_max', UInt64),
             ('tx_gas_cost', Float64),
             ('block_datetime', Datetime(time_unit='us', time_zone=None)),
             ('block_gas_premium', Float64),
             ('blockspace_percentile', Float64),
             ('rounded_blockspace_percent

### Base gas fee volatility is the asset that is being bought/sold.

Preconfirmations are critical to securing future blockspace at less volatile gas prices. This section uses a rolling daily (7200 blocks) average base gas fee as the "breakeven" point. A preconfirmation is the right, but not obligation, to reserve future blockspace at the breakeven price. A future contract "in the money" would be when the future block base gas > breakeven gas price and being "out of money" would be whent he future block base gas < breakeven gas price and the future expires worthless. 

In [ ]:
blocks_df = blocks_lf.collect(streaming=True)

In [ ]:
# mean block gas values
mean_block_vals = blocks_df.sort(by="block_datetime").with_columns(
    (pl.col("base_fee_per_gas").rolling_mean(window_size=7200)).alias(
        "avg_base_fee_daily"
    ),
    (pl.col("base_fee_per_gas").rolling_mean(window_size=5)).alias(
        "avg_base_fee_minute"
    ),  # calculates rolling average over 5 blocks (1 minute)
)

mean_block_vals.mean().select("gas_used", "avg_base_fee_daily", "avg_base_fee_minute")

shape: (1, 3)
┌────────────────────┬────────────────────┬─────────────────────┐
│ gas_used           ┆ avg_base_fee_daily ┆ avg_base_fee_minute │
│ ---                ┆ ---                ┆ ---                 │
│ f64                ┆ f64                ┆ f64                 │
╞════════════════════╪════════════════════╪═════════════════════╡
│ 15.120564535669967 ┆ 12.589467136167862 ┆ 12.613622453882948  │
└────────────────────┴────────────────────┴─────────────────────┘

In [ ]:
itm_count = (
    blocks_df.sort(by="block_datetime")
    .with_columns(
        (pl.col("base_fee_per_gas") - mean_block_vals["avg_base_fee_daily"]).alias(
            "mean_gas_delta_daily"
        )  # negative is "out of money". positive is "in the money"
    )
    .filter(pl.col("mean_gas_delta_daily") > 0)
)

otm_count = (
    blocks_df.sort(by="block_datetime")
    .with_columns(
        (pl.col("base_fee_per_gas") - mean_block_vals["avg_base_fee_daily"]).alias(
            "mean_gas_delta_daily"
        )  # negative is "out of money". positive is "in the money"
    )
    .filter(pl.col("mean_gas_delta_daily") < 0)
)


print(
    f"in the money: {itm_count.shape[0]}, {itm_count.select('mean_gas_delta_daily').sum().item()} gas (gwei)"
)

print(
    f"out of the money: {otm_count.shape[0]}, {otm_count.select('mean_gas_delta_daily').sum().item()} gas (gwei)"
)

in the money: 92438, 868349.2646429302 gas (gwei)
out of the money: 210562, -860985.9495222494 gas (gwei)


In [ ]:
# using the above results, we append the blocks_df gas rolling averages to the sequencer tx dataset
explore_df_gas_vol = mean_block_vals.join(explore_df, on="block_number", how="left")

In [ ]:
explore_df_gas_vol.columns

['author',
 'block_number',
 'timestamp',
 'gas_used',
 'base_fee_per_gas',
 'block_datetime',
 'avg_base_fee_daily',
 'avg_base_fee_minute',
 'transaction_index',
 'transaction_hash',
 'nonce',
 'from_address',
 'to_address',
 'gas_limit',
 'gas_used_right',
 'transaction_type',
 'success',
 'n_input_bytes',
 'n_input_zero_bytes',
 'n_input_nonzero_bytes',
 'n_rlp_bytes',
 'chain_id',
 'author_right',
 'gas_used_block',
 'transaction_index_max',
 'tx_gas_cost',
 'block_datetime_right',
 'block_gas_premium',
 'blockspace_percentile',
 'rounded_blockspace_percentile',
 'gas_price_gwei',
 'max_priority_fee_per_gas_gwei',
 'max_fee_per_gas_gwei',
 'base_fee_per_gas_gwei',
 'block_encoded_kbytes',
 'block_calldata_kbytes',
 'sequencer_names']

In [ ]:
# prototype construction
(
    explore_df_gas_vol.filter(~pl.col("sequencer_names").is_null())
    .select(
        "block_number",
        "sequencer_names",
        "base_fee_per_gas_gwei",
        "avg_base_fee_daily",
        "avg_base_fee_minute",
        "gas_price_gwei",
        "gas_used_right",
        "tx_gas_cost",
    )
    .with_columns(
        (pl.col("avg_base_fee_daily") * pl.col("gas_used_right") / 10**9).alias(
            "tx_gas_cost_avg_daily"
        ),
        (pl.col("avg_base_fee_minute") * pl.col("gas_used_right") / 10**9).alias(
            "tx_gas_cost_avg_minute"
        ),
    )
    .sort(by="block_number")
).head(5)

shape: (5, 10)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ block_num ┆ sequencer ┆ base_fee_ ┆ avg_base_ ┆ … ┆ gas_used_ ┆ tx_gas_co ┆ tx_gas_co ┆ tx_gas_c │
│ ber       ┆ _names    ┆ per_gas_g ┆ fee_daily ┆   ┆ right     ┆ st        ┆ st_avg_da ┆ ost_avg_ │
│ ---       ┆ ---       ┆ wei       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ily       ┆ minute   │
│ u32       ┆ str       ┆ ---       ┆ f64       ┆   ┆ u64       ┆ f64       ┆ ---       ┆ ---      │
│           ┆           ┆ f64       ┆           ┆   ┆           ┆           ┆ f64       ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 18030002  ┆ base      ┆ 32.024751 ┆ null      ┆ … ┆ 578204    ┆ 0.0185457 ┆ null      ┆ null     │
│           ┆           ┆ 684       ┆           ┆   ┆           ┆ 497226955 ┆           ┆          │
│           ┆           ┆           ┆           ┆   ┆           ┆ 36        ┆           ┆          │
│ 18030006  ┆ arbitrum  ┆ 32.722553 ┆ null      ┆ … ┆ 1844309   ┆ 0.0604427 ┆ null      ┆ 0.059902 │
│           ┆           ┆ 091       ┆           ┆   ┆           ┆ 146187091 ┆           ┆ 85106841 │
│           ┆           ┆           ┆           ┆   ┆           ┆ 2         ┆           ┆ 743      │
│ 18030006  ┆ optimism  ┆ 32.722553 ┆ null      ┆ … ┆ 1836180   ┆ 0.0601763 ┆ null      ┆ 0.059638 │
│           ┆           ┆ 091       ┆           ┆   ┆           ┆ 065346323 ┆           ┆ 82249384 │
│           ┆           ┆           ┆           ┆   ┆           ┆ 86        ┆           ┆ 822      │
│ 18030007  ┆ base      ┆ 33.275658 ┆ null      ┆ … ┆ 636948    ┆ 0.0212267 ┆ null      ┆ 0.020847 │
│           ┆           ┆ 042       ┆           ┆   ┆           ┆ 112385358 ┆           ┆ 31807931 │
│           ┆           ┆           ┆           ┆   ┆           ┆ 15        ┆           ┆ 96       │
│ 18030012  ┆ base      ┆ 34.617542 ┆ null      ┆ … ┆ 724572    ┆ 0.0251191 ┆ null      ┆ 0.024371 │
│           ┆           ┆ 597       ┆           ┆   ┆           ┆ 306745934 ┆           ┆ 88540321 │
│           ┆           ┆           ┆           ┆   ┆           ┆ 85        ┆           ┆ 8434     │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [ ]:
# cost adjustment
adj_block_gas: pl.DataFrame = (
    (
        explore_df_gas_vol.filter(~pl.col("sequencer_names").is_null())
        .select(
            "block_number",
            "sequencer_names",
            "base_fee_per_gas_gwei",
            "avg_base_fee_daily",
            "avg_base_fee_minute",
            "gas_price_gwei",
            "gas_used_right",
            "tx_gas_cost",
        )
        .with_columns(
            (pl.col("avg_base_fee_daily") * pl.col("gas_used_right") / 10**9).alias(
                "tx_gas_cost_avg_daily"
            ),
            (pl.col("avg_base_fee_minute") * pl.col("gas_used_right") / 10**9).alias(
                "tx_gas_cost_avg_minute"
            ),
        )
        .with_columns(
            # ITM when positive, OTM when negative
            (pl.col("tx_gas_cost") - pl.col("tx_gas_cost_avg_daily")).alias(
                "tx_gas_cost_delta_daily"
            ),
            (pl.col("tx_gas_cost") - pl.col("tx_gas_cost_avg_minute")).alias(
                "tx_gas_cost_delta_minute"
            ),
        )
    )
    .select(
        "block_number",
        "sequencer_names",
        "tx_gas_cost_delta_daily",
        "tx_gas_cost_delta_minute",
    )
    .group_by("sequencer_names")
    .agg(
        pl.col("tx_gas_cost_delta_daily").sum().alias("tx_gas_cost_delta_daily_sum"),
        pl.col("tx_gas_cost_delta_minute").sum().alias("tx_gas_cost_delta_minute_sum"),
    )
)

adj_block_gas

shape: (7, 3)
┌─────────────────┬─────────────────────────────┬──────────────────────────────┐
│ sequencer_names ┆ tx_gas_cost_delta_daily_sum ┆ tx_gas_cost_delta_minute_sum │
│ ---             ┆ ---                         ┆ ---                          │
│ str             ┆ f64                         ┆ f64                          │
╞═════════════════╪═════════════════════════════╪══════════════════════════════╡
│ mantle          ┆ -9.144422926214286          ┆ 1.679253692288393            │
│ linea           ┆ 1.0423141583801456          ┆ -0.3072991952510987          │
│ polygon_zkevm   ┆ -2.397012205483913          ┆ 0.23654061516279626          │
│ base            ┆ 7.810627296202728           ┆ 2.7664776559462716           │
│ arbitrum        ┆ 2.667095412723976           ┆ 5.127072386666014            │
│ starknet        ┆ 267.1387349156266           ┆ 83.20356869636893            │
│ optimism        ┆ -0.10416798710956021        ┆ 1.862359719906382            │
└─────────────────┴─────────────────────────────┴──────────────────────────────┘

### Aggregate Sequencer Stats

This section is an overview of Sequencer activity on Ethereum such as how many transactions they submit, how much gas they consumed, and how much calldata they are saving.

In [ ]:
def agg_sequencer_stats(df: pl.DataFrame):
    """
    Prints aggregate sequencer statistics
    """
    return (
        df.group_by(["block_number", "sequencer_names"])
        .agg(
            pl.count().alias("n_txs"),
            pl.col("gas_used_block").sum().alias("sequencer_gas_used"),
            pl.col("tx_gas_cost").sum().alias("tx_gas_cost_sum_eth"),
            pl.col("n_input_bytes").sum().alias("sequencer_n_input_bytes_sum"),
            pl.col("n_input_zero_bytes")
            .sum()
            .alias("sequencer_n_input_zero_bytes_sum"),
            pl.col("n_input_nonzero_bytes")
            .mean()
            .alias("sequencer_n_input_nonzero_bytes_mean"),
            pl.col("n_rlp_bytes").sum().alias("sequencer_n_rlp_bytes_sum"),
            pl.col("gas_price_gwei").mean().alias("sequencer_gas_price_mean"),
            # ! Currently not used - selecting columns that are the same for all rows in the group
            pl.col("base_fee_per_gas_gwei").first(),
            pl.col("block_datetime").first(),
            pl.col("block_encoded_kbytes").first(),
            pl.col("block_calldata_kbytes").first(),
        )
        .group_by(["sequencer_names"])
        .agg(
            pl.col("block_number").count().alias("n_blocks"),
            pl.col("n_txs").sum(),
            pl.col("tx_gas_cost_sum_eth").sum().round(2),
            pl.col("sequencer_n_input_bytes_sum").sum(),
            pl.col("sequencer_n_input_zero_bytes_sum").sum(),
            pl.col("sequencer_n_input_nonzero_bytes_mean").mean().round(2),
            pl.col("sequencer_n_rlp_bytes_sum").sum(),
            pl.col("sequencer_gas_price_mean").mean().round(2),
        )
        .with_columns(
            (pl.col("sequencer_n_input_bytes_sum") / 10**6)
            .alias("n_input_mbytes_sum")
            .round(2),
            (pl.col("sequencer_n_rlp_bytes_sum") / 10**6)
            .alias("n_rlp_mbytes_sum")
            .round(2),
        )
        .drop("sequencer_n_input_bytes_sum", "sequencer_n_rlp_bytes_sum")
    )

**aggregate sequencer stats pre EIP-4844** - The below table shows aggregate sequencer statistics for block usage.

In [ ]:
agg_seq_stats = (
    agg_sequencer_stats(explore_df)
    .with_columns(
        (pl.col("n_rlp_mbytes_sum") / pl.col("tx_gas_cost_sum_eth"))
        .alias("mb_data_per_eth")
        .round(2),
    )
    .sort(by="mb_data_per_eth", descending=True)
).select(
    "sequencer_names",
    "n_blocks",
    "n_txs",
    "tx_gas_cost_sum_eth",
    "mb_data_per_eth",
    "n_input_mbytes_sum",
)

agg_seq_stats.join(adj_block_gas, on="sequencer_names", how="left").rename(
    {
        "sequencer_names": "sequencer",
        "mb_data_per_eth": "mb_per_eth",
        "n_input_mbytes_sum": "total_mbytes",
        "tx_gas_cost_sum_eth": "tota_cost_eth",
    }
).sort(by="n_txs", descending=True)

shape: (7, 8)
┌─────────────┬──────────┬────────┬────────────┬────────────┬────────────┬────────────┬────────────┐
│ sequencer   ┆ n_blocks ┆ n_txs  ┆ tota_cost_ ┆ mb_per_eth ┆ total_mbyt ┆ tx_gas_cos ┆ tx_gas_cos │
│ ---         ┆ ---      ┆ ---    ┆ eth        ┆ ---        ┆ es         ┆ t_delta_da ┆ t_delta_mi │
│ str         ┆ u32      ┆ u32    ┆ ---        ┆ f64        ┆ ---        ┆ ily_sum    ┆ nute_sum   │
│             ┆          ┆        ┆ f64        ┆            ┆ f64        ┆ ---        ┆ ---        │
│             ┆          ┆        ┆            ┆            ┆            ┆ f64        ┆ f64        │
╞═════════════╪══════════╪════════╪════════════╪════════════╪════════════╪════════════╪════════════╡
│ starknet    ┆ 89200    ┆ 176263 ┆ 1435.82    ┆ 0.63       ┆ 885.22     ┆ 267.138734 ┆ 83.2035686 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 9156266    ┆ 9636893    │
│ base        ┆ 38315    ┆ 39440  ┆ 537.96     ┆ 4.36       ┆ 2339.36    ┆ 7.81062729 ┆ 2.76647765 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 6202728    ┆ 59462716   │
│ linea       ┆ 21864    ┆ 31260  ┆ 435.03     ┆ 4.46       ┆ 1938.02    ┆ 1.04231415 ┆ -0.3072991 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 83801456   ┆ 952510987  │
│ arbitrum    ┆ 14961    ┆ 23686  ┆ 603.92     ┆ 3.88       ┆ 2340.73    ┆ 2.66709541 ┆ 5.12707238 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 2723976    ┆ 6666014    │
│ optimism    ┆ 15344    ┆ 15354  ┆ 401.3      ┆ 4.41       ┆ 1769.85    ┆ -0.1041679 ┆ 1.86235971 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 8710956021 ┆ 9906382    │
│ polygon_zke ┆ 4024     ┆ 4024   ┆ 70.14      ┆ 5.47       ┆ 382.9      ┆ -2.3970122 ┆ 0.23654061 │
│ vm          ┆          ┆        ┆            ┆            ┆            ┆ 05483913   ┆ 516279626  │
│ mantle      ┆ 2018     ┆ 2018   ┆ 124.9      ┆ 1.54       ┆ 191.76     ┆ -9.1444229 ┆ 1.67925369 │
│             ┆          ┆        ┆            ┆            ┆            ┆ 26214286   ┆ 2288393    │
└─────────────┴──────────┴────────┴────────────┴────────────┴────────────┴────────────┴────────────┘

### Variable Sequencer Stats

To see the variable sequencer stats, it seems most efficient to create a function, compute numbers for a single sequencer, and then combine with other sequencer calculations. 

In [ ]:
def variable_sequencer_stats(df: pl.DataFrame, sequencer_name: str) -> pl.DataFrame:
    return (
        df.filter(pl.col("sequencer_names") == sequencer_name)
        .sort(by="block_number")
        .with_columns(
            (pl.col("block_number").diff(n=1)).alias("block_number_diff"),
            (pl.col("n_input_nonzero_bytes").diff(n=1)).alias(
                "n_input_nonzero_bytes_diff"
            ),
            (pl.col("n_input_zero_bytes").diff(n=1)).alias("n_input_zero_bytes_diff"),
            (pl.col("gas_used").diff(n=1)).alias("gas_used_diff"),
            (pl.col("base_fee_per_gas_gwei").diff(n=1)).alias(
                "base_fee_per_gas_gwei_diff"
            ),
        )
        .select(
            "sequencer_names",
            "block_number",
            "block_number_diff",
            "n_input_nonzero_bytes_diff",
            "n_input_zero_bytes_diff",
            "gas_used_diff",
            "base_fee_per_gas_gwei_diff",
        )
    )

In [ ]:
variable_seq_dfs_list: list[pl.DataFrame] = []
for name in sequencers_l2["sequencer_names"]:
    df: pl.DataFrame = variable_sequencer_stats(explore_df, name)
    variable_seq_dfs_list.append(df)

In [ ]:
concat_df = pl.concat(variable_seq_dfs_list)

In [ ]:
# example of multiple transactions in the same block
explore_df.filter(pl.col("block_number") == 18072641).filter(
    pl.col("sequencer_names") == "arbitrum"
)

shape: (3, 30)
┌────────────┬────────────┬───────────┬────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ block_numb ┆ transactio ┆ transacti ┆ nonce  ┆ … ┆ base_fee_ ┆ block_enc ┆ block_cal ┆ sequencer │
│ er         ┆ n_index    ┆ on_hash   ┆ ---    ┆   ┆ per_gas_g ┆ oded_kbyt ┆ ldata_kby ┆ _names    │
│ ---        ┆ ---        ┆ ---       ┆ u64    ┆   ┆ wei       ┆ es        ┆ tes       ┆ ---       │
│ u32        ┆ u64        ┆ str       ┆        ┆   ┆ ---       ┆ ---       ┆ ---       ┆ str       │
│            ┆            ┆           ┆        ┆   ┆ f64       ┆ f64       ┆ f64       ┆           │
╞════════════╪════════════╪═══════════╪════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 18072641   ┆ 131        ┆ 0x24add26 ┆ 282983 ┆ … ┆ 59.166738 ┆ 416.252   ┆ 399.129   ┆ arbitrum  │
│            ┆            ┆ cf55e50e0 ┆        ┆   ┆ 431       ┆           ┆           ┆           │
│            ┆            ┆ fa15092a0 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 3c307b026 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ f060ffc83 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ f1802da8e ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 5b3f8a5da ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 65d       ┆        ┆   ┆           ┆           ┆           ┆           │
│ 18072641   ┆ 132        ┆ 0xfeb920a ┆ 282984 ┆ … ┆ 59.166738 ┆ 416.252   ┆ 399.129   ┆ arbitrum  │
│            ┆            ┆ e55beab0a ┆        ┆   ┆ 431       ┆           ┆           ┆           │
│            ┆            ┆ 66680a54a ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 244368b13 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 7e3d7d914 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 563bab603 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 7ec0fc32f ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ a97       ┆        ┆   ┆           ┆           ┆           ┆           │
│ 18072641   ┆ 130        ┆ 0x25a3cac ┆ 282982 ┆ … ┆ 59.166738 ┆ 416.252   ┆ 399.129   ┆ arbitrum  │
│            ┆            ┆ 498260b62 ┆        ┆   ┆ 431       ┆           ┆           ┆           │
│            ┆            ┆ fa772eca9 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ c50ee9feb ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 1d8ab59b1 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 4300cc69d ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 238352457 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 827       ┆        ┆   ┆           ┆           ┆           ┆           │
└────────────┴────────────┴───────────┴────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [ ]:
# very high base gas difference
explore_df.filter(pl.col("block_number") == 18183437).filter(
    pl.col("sequencer_names") == "arbitrum"
)

shape: (3, 30)
┌────────────┬────────────┬───────────┬────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ block_numb ┆ transactio ┆ transacti ┆ nonce  ┆ … ┆ base_fee_ ┆ block_enc ┆ block_cal ┆ sequencer │
│ er         ┆ n_index    ┆ on_hash   ┆ ---    ┆   ┆ per_gas_g ┆ oded_kbyt ┆ ldata_kby ┆ _names    │
│ ---        ┆ ---        ┆ ---       ┆ u64    ┆   ┆ wei       ┆ es        ┆ tes       ┆ ---       │
│ u32        ┆ u64        ┆ str       ┆        ┆   ┆ ---       ┆ ---       ┆ ---       ┆ str       │
│            ┆            ┆           ┆        ┆   ┆ f64       ┆ f64       ┆ f64       ┆           │
╞════════════╪════════════╪═══════════╪════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 18183437   ┆ 222        ┆ 0xed8384f ┆ 296261 ┆ … ┆ 225.07265 ┆ 354.016   ┆ 314.434   ┆ arbitrum  │
│            ┆            ┆ ed8185931 ┆        ┆   ┆ 5352      ┆           ┆           ┆           │
│            ┆            ┆ cf39f404a ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 152fd6376 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 14010accd ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ ee56d62f2 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 21c4e43d9 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 68d       ┆        ┆   ┆           ┆           ┆           ┆           │
│ 18183437   ┆ 223        ┆ 0x3015787 ┆ 296262 ┆ … ┆ 225.07265 ┆ 354.016   ┆ 314.434   ┆ arbitrum  │
│            ┆            ┆ e357d9cf2 ┆        ┆   ┆ 5352      ┆           ┆           ┆           │
│            ┆            ┆ 278a0a999 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ e2d8aca64 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 4eb4ea3d4 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 32ca92dbd ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 237d724d1 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ a3b       ┆        ┆   ┆           ┆           ┆           ┆           │
│ 18183437   ┆ 3          ┆ 0xd1f0a50 ┆ 296260 ┆ … ┆ 225.07265 ┆ 354.016   ┆ 314.434   ┆ arbitrum  │
│            ┆            ┆ 32d1f27f7 ┆        ┆   ┆ 5352      ┆           ┆           ┆           │
│            ┆            ┆ 716ca3135 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 2b48b283e ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ d8376c199 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 04b16791c ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 2a9481bb4 ┆        ┆   ┆           ┆           ┆           ┆           │
│            ┆            ┆ 956       ┆        ┆   ┆           ┆           ┆           ┆           │
└────────────┴────────────┴───────────┴────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [ ]:
# check gas difference betwen a small block range
# very high base gas difference
explore_df.filter(pl.col("block_number") > 18183327).filter(
    pl.col("block_number") < 18183477
).sort(by="block_number").plot.line(
    x="block_number",
    y="base_fee_per_gas_gwei",
    height=500,
    width=600,
    title="150 block range",
)

:Curve   [block_number]   (base_fee_per_gas_gwei)

In [ ]:
# NOTE - there's an interesting pattern where sequencers will submit multiple transactions in the same block. We can filter for this with `.filter(pl.col("block_number_diff") == 0)`
concat_df.filter(pl.col("block_number_diff") < 60).sort(
    by="base_fee_per_gas_gwei_diff", descending=True
)

shape: (289_682, 7)
┌──────────────┬─────────────┬─────────────┬─────────────┬─────────────┬─────────────┬─────────────┐
│ sequencer_na ┆ block_numbe ┆ block_numbe ┆ n_input_non ┆ n_input_zer ┆ gas_used_di ┆ base_fee_pe │
│ mes          ┆ r           ┆ r_diff      ┆ zero_bytes_ ┆ o_bytes_dif ┆ ff          ┆ r_gas_gwei_ │
│ ---          ┆ ---         ┆ ---         ┆ diff        ┆ f           ┆ ---         ┆ diff        │
│ str          ┆ u32         ┆ i64         ┆ ---         ┆ ---         ┆ i64         ┆ ---         │
│              ┆             ┆             ┆ i64         ┆ i64         ┆             ┆ f64         │
╞══════════════╪═════════════╪═════════════╪═════════════╪═════════════╪═════════════╪═════════════╡
│ polygon_zkev ┆ 18114960    ┆ 55          ┆ -4459       ┆ -9813       ┆ -144553     ┆ 373.0448513 │
│ m            ┆             ┆             ┆             ┆             ┆             ┆ 2800005     │
│ optimism     ┆ 18114948    ┆ 20          ┆ -267        ┆ -102        ┆ -4680       ┆ 243.2360088 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 71          │
│ base         ┆ 18114948    ┆ 14          ┆ -11473      ┆ -92         ┆ -183936     ┆ 220.4697479 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 89          │
│ arbitrum     ┆ 18183437    ┆ 59          ┆ -473        ┆ 25          ┆ -5265       ┆ 199.4418414 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 9699998     │
│ …            ┆ …           ┆ …           ┆ …           ┆ …           ┆ …           ┆ …           │
│ optimism     ┆ 18183574    ┆ 24          ┆ 399         ┆ -22         ┆ 6296        ┆ -89.1279882 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 27          │
│ optimism     ┆ 18183492    ┆ 19          ┆ 251         ┆ -33         ┆ 3884        ┆ -108.936709 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 36700002    │
│ optimism     ┆ 18114973    ┆ 9           ┆ -956        ┆ -94         ┆ -15672      ┆ -108.995093 │
│              ┆             ┆             ┆             ┆             ┆             ┆ 60000002    │
│ polygon_zkev ┆ 18115016    ┆ 56          ┆ -3368       ┆ -3512       ┆ -89773      ┆ -303.093530 │
│ m            ┆             ┆             ┆             ┆             ┆             ┆ 57500005    │
└──────────────┴─────────────┴─────────────┴─────────────┴─────────────┴─────────────┴─────────────┘

In [ ]:
concat_df.filter(pl.col("block_number_diff") < 60).sort(by="block_number").group_by(
    "sequencer_names"
).agg(
    pl.col("base_fee_per_gas_gwei_diff")
    .abs()
    .mean()
    .alias("base_fee_per_gas_gwei_diff_mean_abs"),
    pl.col("base_fee_per_gas_gwei_diff")
    .abs()
    .max()
    .alias("base_fee_per_gas_gwei_diff_max"),
    pl.col("n_input_nonzero_bytes_diff")
    .abs()
    .mean()
    .alias("n_input_nonzero_bytes_mean_abs"),
)

shape: (7, 4)
┌─────────────────┬──────────────────────────┬──────────────────────────┬──────────────────────────┐
│ sequencer_names ┆ base_fee_per_gas_gwei_di ┆ base_fee_per_gas_gwei_di ┆ n_input_nonzero_bytes_me │
│ ---             ┆ ff_mean_abs              ┆ ff_max                   ┆ an_abs                   │
│ str             ┆ ---                      ┆ ---                      ┆ ---                      │
│                 ┆ f64                      ┆ f64                      ┆ f64                      │
╞═════════════════╪══════════════════════════╪══════════════════════════╪══════════════════════════╡
│ base            ┆ 0.8412222719914758       ┆ 220.469747989            ┆ 11287.56922881786        │
│ linea           ┆ 0.5144804805574005       ┆ 12.692291840000001       ┆ 2938.934922266478        │
│ polygon_zkevm   ┆ 2.023582698155695        ┆ 373.04485132800005       ┆ 14620.346080305928       │
│ arbitrum        ┆ 0.7975138688615676       ┆ 199.44184149699998       ┆ 698.6699767589267        │
│ starknet        ┆ 0.2436989020797321       ┆ 38.571344432000004       ┆ 25489.295828740895       │
│ optimism        ┆ 1.3023106947318552       ┆ 243.236008871            ┆ 1642.3571568307793       │
│ mantle          ┆ 1.0069630139010988       ┆ 88.027535683             ┆ 764.6813186813187        │
└─────────────────┴──────────────────────────┴──────────────────────────┴──────────────────────────┘

In [ ]:
explore_df.filter(pl.col("sequencer_names") == "base").sort(
    by="block_number"
).with_columns((pl.col("block_number").diff(n=2)).alias("block_number_diff")).filter(
    pl.col("block_number_diff") < 5
).select(
    "block_number_diff"
).plot.hist(
    height=600,
    width=800,
)

:Histogram   [block_number_diff]   (block_number_diff_count)

In [ ]:
# what should the interval range be for diff? Right now the default is one transaction.
# 300 blocks = 1hr...

tx_count_range = 5  # rolling average over `n` transactions
(
    explore_df.sort(by="block_datetime")
    .group_by("sequencer_names")
    .agg(
        pl.col("block_datetime").diff(tx_count_range).mean().alias("tx_time_diff_mean"),
        pl.col("block_number")
        .diff(tx_count_range)
        .mean()
        .alias("block_number_diff_mean"),
        pl.col("gas_used").diff(tx_count_range).mean().alias("gas_used_diff_mean"),
        pl.col("n_input_bytes")
        .diff(tx_count_range)
        .mean()
        .alias("n_input_bytes_diff_mean"),
        pl.col("block_datetime").diff(tx_count_range).std().alias("tx_time_diff_std"),
        pl.col("block_number")
        .diff(tx_count_range)
        .std()
        .alias("block_number_diff_std"),
        pl.col("gas_used").diff(tx_count_range).std().alias("gas_used_diff_std"),
        pl.col("n_input_bytes")
        .diff(tx_count_range)
        .std()
        .alias("n_input_bytes_diff_std"),
        pl.col("tx_gas_cost").mean().alias("tx_gas_cost_mean"),
    )
)

shape: (7, 10)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ sequencer ┆ tx_time_d ┆ block_num ┆ gas_used_ ┆ … ┆ block_num ┆ gas_used_ ┆ n_input_b ┆ tx_gas_c │
│ _names    ┆ iff_mean  ┆ ber_diff_ ┆ diff_mean ┆   ┆ ber_diff_ ┆ diff_std  ┆ ytes_diff ┆ ost_mean │
│ ---       ┆ ---       ┆ mean      ┆ ---       ┆   ┆ std       ┆ ---       ┆ _std      ┆ ---      │
│ str       ┆ duration[ ┆ ---       ┆ f64       ┆   ┆ ---       ┆ f64       ┆ ---       ┆ f64      │
│           ┆ μs]       ┆ f64       ┆           ┆   ┆ f64       ┆           ┆ f64       ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ mantle    ┆ 1h 52m    ┆ 557.33084 ┆ 9345.5037 ┆ … ┆ 769.04925 ┆ 895430.26 ┆ 19281.541 ┆ 0.061894 │
│           ┆ 30s       ┆ 94783904  ┆ 25782415  ┆   ┆ 60801673  ┆ 4199491   ┆ 96207355  ┆ 57524087 │
│           ┆ 396423µs  ┆           ┆           ┆   ┆           ┆           ┆           ┆ 065      │
│ linea     ┆ 7m 15s    ┆ 35.982786 ┆ -4.068852 ┆ … ┆ 208.15977 ┆ 127074.30 ┆ 9748.4941 ┆ 0.013916 │
│           ┆ 824796µs  ┆ 75411934  ┆ 983522636 ┆   ┆ 392557673 ┆ 863639007 ┆ 22239095  ┆ 60664874 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 006      │
│ optimism  ┆ 14m 47s   ┆ 73.276760 ┆ 5.7780962 ┆ … ┆ 268.40465 ┆ 55504.803 ┆ 3480.5719 ┆ 0.026136 │
│           ┆ 527786µs  ┆ 70102287  ┆ 929181054 ┆   ┆ 323571846 ┆ 210741455 ┆ 94783157  ┆ 67562310 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 1117     │
│ starknet  ┆ 1m 17s    ┆ 6.3717505 ┆ 41.814867 ┆ … ┆ 90.631390 ┆ 855655.31 ┆ 43794.541 ┆ 0.008145 │
│           ┆ 174505µs  ┆ 02104869  ┆ 97762371  ┆   ┆ 64723313  ┆ 69131503  ┆ 561320664 ┆ 87305068 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 2878     │
│ polygon_z ┆ 56m 27s   ┆ 279.64419 ┆ 855.08982 ┆ … ┆ 523.32571 ┆ 541464.95 ┆ 44105.128 ┆ 0.017429 │
│ kevm      ┆ 42547µs   ┆ 00970391  ┆ 33391391  ┆   ┆ 23365839  ┆ 28251381  ┆ 69976501  ┆ 32285765 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 2793     │
│ base      ┆ 5m 45s    ┆ 28.525041 ┆ 24.402282 ┆ … ┆ 167.11611 ┆ 466491.96 ┆ 29270.252 ┆ 0.013640 │
│           ┆ 495625µs  ┆ 207049576 ┆ 23659186  ┆   ┆ 035583238 ┆ 370882797 ┆ 989011697 ┆ 07096830 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 446      │
│ arbitrum  ┆ 9m 35s    ┆ 47.494658 ┆ -4.158354 ┆ … ┆ 216.44450 ┆ 29872.170 ┆ 1729.4699 ┆ 0.025496 │
│           ┆ 254085µs  ┆ 16477345  ┆ 799206115 ┆   ┆ 180999695 ┆ 953157263 ┆ 420581398 ┆ 78729458 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 7476     │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [ ]:
# what should the interval range be for diff? Right now the default is one transaction.
# 300 blocks = 1hr...

tx_count_range = 50  # rolling average over `n` transactions
(
    explore_df.sort(by="block_datetime")
    .group_by("sequencer_names")
    .agg(
        pl.col("block_datetime").diff(tx_count_range).mean().alias("tx_time_diff_mean"),
        pl.col("block_number")
        .diff(tx_count_range)
        .mean()
        .alias("block_number_diff_mean"),
        pl.col("gas_used").diff(tx_count_range).mean().alias("gas_used_diff_mean"),
        pl.col("n_input_bytes")
        .diff(tx_count_range)
        .mean()
        .alias("n_input_bytes_diff_mean"),
        pl.col("block_datetime").diff(tx_count_range).std().alias("tx_time_diff_std"),
        pl.col("block_number")
        .diff(tx_count_range)
        .std()
        .alias("block_number_diff_std"),
        pl.col("gas_used").diff(tx_count_range).std().alias("gas_used_diff_std"),
        pl.col("n_input_bytes")
        .diff(tx_count_range)
        .std()
        .alias("n_input_bytes_diff_std"),
        pl.col("tx_gas_cost").mean().alias("tx_gas_cost_mean"),
    )
)

shape: (7, 10)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ sequencer ┆ tx_time_d ┆ block_num ┆ gas_used_ ┆ … ┆ block_num ┆ gas_used_ ┆ n_input_b ┆ tx_gas_c │
│ _names    ┆ iff_mean  ┆ ber_diff_ ┆ diff_mean ┆   ┆ ber_diff_ ┆ diff_std  ┆ ytes_diff ┆ ost_mean │
│ ---       ┆ ---       ┆ mean      ┆ ---       ┆   ┆ std       ┆ ---       ┆ _std      ┆ ---      │
│ str       ┆ duration[ ┆ ---       ┆ f64       ┆   ┆ ---       ┆ f64       ┆ ---       ┆ f64      │
│           ┆ μs]       ┆ f64       ┆           ┆   ┆ f64       ┆           ┆ f64       ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ arbitrum  ┆ 1h 35m    ┆ 475.13073 ┆ -0.235234 ┆ … ┆ 695.53438 ┆ 30256.033 ┆ 1751.5522 ┆ 0.025496 │
│           ┆ 54s       ┆ 278050433 ┆ 388221357 ┆   ┆ 87800959  ┆ 455460896 ┆ 222785373 ┆ 78729458 │
│           ┆ 781350µs  ┆           ┆ 25        ┆   ┆           ┆           ┆           ┆ 7476     │
│ polygon_z ┆ 9h 25m    ┆ 2801.5390 ┆ 2723.4743 ┆ … ┆ 1839.2413 ┆ 622966.81 ┆ 52870.746 ┆ 0.017429 │
│ kevm      ┆ 32s       ┆ 03522899  ┆ 331655764 ┆   ┆ 949776574 ┆ 90244868  ┆ 076809606 ┆ 32285765 │
│           ┆ 349270µs  ┆           ┆           ┆   ┆           ┆           ┆           ┆ 2793     │
│ optimism  ┆ 2h 27m    ┆ 733.00222 ┆ 18.971249 ┆ … ┆ 863.82766 ┆ 59288.427 ┆ 3716.5109 ┆ 0.026136 │
│           ┆ 58s       ┆ 1641401   ┆ 34657606  ┆   ┆ 84981025  ┆ 79303996  ┆ 934314023 ┆ 67562310 │
│           ┆ 158128µs  ┆           ┆           ┆   ┆           ┆           ┆           ┆ 1117     │
│ starknet  ┆ 12m 51s   ┆ 63.726773 ┆ 4.9836504 ┆ … ┆ 284.68557 ┆ 855714.43 ┆ 43958.833 ┆ 0.008145 │
│           ┆ 858103µs  ┆ 847559485 ┆ 68467139  ┆   ┆ 617122957 ┆ 88334951  ┆ 639994155 ┆ 87305068 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 2878     │
│ base      ┆ 57m 35s   ┆ 285.29159 ┆ 387.06128 ┆ … ┆ 527.61836 ┆ 572877.11 ┆ 35945.288 ┆ 0.013640 │
│           ┆ 444325µs  ┆ 68519929  ┆ 458999746 ┆   ┆ 50791231  ┆ 17534011  ┆ 27703577  ┆ 07096830 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 446      │
│ linea     ┆ 1h 12m    ┆ 360.09202 ┆ -28.13159 ┆ … ┆ 682.69602 ┆ 130567.91 ┆ 9901.3743 ┆ 0.013916 │
│           ┆ 41s       ┆ 17878885  ┆ 243832105 ┆   ┆ 1746625   ┆ 037081284 ┆ 53265535  ┆ 60664874 │
│           ┆ 416725µs  ┆           ┆           ┆   ┆           ┆           ┆           ┆ 006      │
│ mantle    ┆ 18h 50m   ┆ 5600.0619 ┆ 39381.757 ┆ … ┆ 3307.0091 ┆ 1028471.9 ┆ 22133.340 ┆ 0.061894 │
│           ┆ 30s       ┆ 918699185 ┆ 113821135 ┆   ┆ 03893865  ┆ 050396975 ┆ 33909879  ┆ 57524087 │
│           ┆ 597560µs  ┆           ┆           ┆   ┆           ┆           ┆           ┆ 065      │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [ ]:
STOP

NameError: name 'STOP' is not defined

### How does EIP-4844 work?
EIP-4844 introduces a new transaction type, called a blob-carrying transaction. A blob-carrying transaction is like a regular transaction, except it also carries an extra piece of data called a blob. Blobs are extremely large (~125 kB), and can be much cheaper than similar amounts of calldata. [source](https://notes.ethereum.org/@vbuterin/proto_danksharding_faq#What-format-is-blob-data-in-and-how-is-it-committed-to). The blob space is a new type of data storage that is not accessible to the Ethereum Virtual Machine (EVM), unlike calldata. Unlike calldata, which is stored in history forever, blobs are persisted in beacon nodes for a short period of time (approximately 2 weeks), which allows them to be priced cheaper.

### Blob Gas Math

Pre EIP-4844 block size in gas at 16 gas per nonzero calldata byte (most expensive type of data) is
$$\frac{30,000,000}{16} = 1.875MB $$

Each blob size is 0.125 MB. The target is 3 blobs (0.375 MB)and the maximum is 6 blobs (0.75 MB) per block. Each blob is worth 131,072 gas [2**17, source](https://eips.ethereum.org/EIPS/eip-4844)

The blob gas limit is 2**17 value which turns out to be 131,072 gas. This is about 1.04 gas per byte, compared to 16 gas per non-zero calldata byte. After EIP-4844, block size in gas will increase to 42,000,000 gas assuming a 16 gas per byte cost similar to calldata. 

### Blob Pricing
Regular gas pricing: The price of gas in a block is a simple function of how much gas was used in the previous block compared to the target.
Blob gas pricing: The price of blob gas is a function of the running tally excess blobs there have been in total. [source](https://domothy.com/blobspace/)

### Blob vs Calldata Tradeoff
The optimal rollup data strategy has two components - cost and delay. First, the base cost of blob data is 16x less expensive than calldata under constant gas conditions, when the gas markets are assumed identical. <span style="color: red;">Second, the blob must be submitted in full whereas calldata can be submitted in arbitrary chunks (is this true?).</span>

## Rollup Calldata Metrics

### Pricing Futures Calldata (Pre EIP-4844)
Since EIP-4844 will lower the gas cost for the calldata, we focus on the gas premium over the base gas fee. It's calculated as `gas_price` / `base_fee_per_gas` - 1 = `base_gas_premium_pct`. 


In [ ]:
# aggregate rollup costs
def rollup_costs(df: pl.DataFrame):
    return (
        df.group_by("sequencer_names")
        .agg(
            pl.col("gas_used").sum().alias("sequencer_gas_used"),
            pl.col("tx_gas_cost").sum().alias("tx_gas_cost_sum_eth"),
            pl.col("gas_used_block").first(),
            pl.col("total_calldata_block_size").first(),
            pl.col("calldata_size").sum().alias("sequencer_calldata_size_sum"),
            pl.col("calldata_size").mean().alias("sequencer_calldata_size_mean_kb"),
            pl.col("block_datetime").diff().mean().alias("post_tx_time_mean"),
            pl.col("block_number").diff().mean().alias("posts_block_number_mean"),
            pl.col("gas_price").mean().alias("gas_price_mean"),
            pl.col("base_fee_per_gas").first().alias("base_fee_per_gas"),
            pl.col("base_fee_per_gas").mean().alias("base_fee_per_gas_mean"),
            pl.count().alias("tx_count"),
        )
        .with_columns(
            [
                (pl.col("sequencer_gas_used") / pl.col("gas_used_block")).alias(
                    "sequencer_gas_utilization"
                ),
                (pl.col("gas_price_mean") / pl.col("base_fee_per_gas") - 1).alias(
                    "base_gas_premium_mean_pct"
                ),
                (pl.col("sequencer_calldata_size_sum") / 10**6).alias(
                    "sequencer_calldata_size_sum_gb"
                ),
            ]
        )
        .sort(by="tx_gas_cost_sum_eth", descending=True)
    ).select(
        "sequencer_names",
        "tx_gas_cost_sum_eth",
        "tx_count",
        "sequencer_calldata_size_sum_gb",
        "sequencer_calldata_size_mean_kb",
        "base_gas_premium_mean_pct",
        "base_fee_per_gas_mean",
        "posts_block_number_mean",
        "post_tx_time_mean",
    )

In [ ]:
rollup_cost_stats = rollup_costs(explore_df)
rollup_cost_stats

shape: (8, 9)
┌───────────┬───────────┬──────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ sequencer ┆ tx_gas_co ┆ tx_count ┆ sequencer ┆ … ┆ base_gas_ ┆ base_fee_ ┆ posts_blo ┆ post_tx_t │
│ _names    ┆ st_sum_et ┆ ---      ┆ _calldata ┆   ┆ premium_m ┆ per_gas_m ┆ ck_number ┆ ime_mean  │
│ ---       ┆ h         ┆ u32      ┆ _size_sum ┆   ┆ ean_pct   ┆ ean       ┆ _mean     ┆ ---       │
│ str       ┆ ---       ┆          ┆ _gb       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ duration[ │
│           ┆ f64       ┆          ┆ ---       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ μs]       │
│           ┆           ┆          ┆ f64       ┆   ┆           ┆           ┆           ┆           │
╞═══════════╪═══════════╪══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ linea     ┆ 4165.5748 ┆ 120184   ┆ 17.821789 ┆ … ┆ 0.2801574 ┆ 32.859871 ┆ 1.7426091 ┆ 21s       │
│           ┆ 11471807  ┆          ┆ 624000033 ┆   ┆ 723752000 ┆ 859515486 ┆ 87655492  ┆ 145353µs  │
│           ┆           ┆          ┆           ┆   ┆ 6         ┆           ┆           ┆           │
│ arbitrum  ┆ 3796.9360 ┆ 52164    ┆ 10.224386 ┆ … ┆ 0.8761479 ┆ 39.358768 ┆ 4.0197649 ┆ 48s       │
│           ┆ 026585096 ┆          ┆ 467999949 ┆   ┆ 21898643  ┆ 72583072  ┆ 675057034 ┆ 777332µs  │
│ optimism  ┆ 1564.5296 ┆ 25584    ┆ 5.8688649 ┆ … ┆ 0.5088555 ┆ 33.039729 ┆ 8.1753117 ┆ 1m 39s    │
│           ┆ 36044541  ┆          ┆ 2200002   ┆   ┆ 307138645 ┆ 85870466  ┆ 30446     ┆ 201813µs  │
│ scroll    ┆ 943.86447 ┆ 21660    ┆ 4.4651379 ┆ … ┆ 0.3443830 ┆ 29.914249 ┆ 9.6606029 ┆ 1m 57s    │
│           ┆ 77635262  ┆          ┆ 80000031  ┆   ┆ 452740863 ┆ 929707925 ┆ 82593842  ┆ 224802µs  │
│           ┆           ┆          ┆           ┆   ┆ 6         ┆           ┆           ┆           │
│ starknet  ┆ 925.31248 ┆ 88967    ┆ 3.2072467 ┆ … ┆ 0.4719869 ┆ 32.160838 ┆ 2.3566306 ┆ 28s       │
│           ┆ 72041083  ┆          ┆ 190004996 ┆   ┆ 628482500 ┆ 320304585 ┆ 229346043 ┆ 596137µs  │
│           ┆           ┆          ┆           ┆   ┆ 4         ┆           ┆           ┆           │
│ base      ┆ 782.54577 ┆ 42001    ┆ 3.1439878 ┆ … ┆ 0.4161816 ┆ 32.459257 ┆ 4.9921190 ┆ 1m 576ms  │
│           ┆ 81998224  ┆          ┆ 529999885 ┆   ┆ 672628986 ┆ 65840359  ┆ 47619048  ┆           │
│ mantle    ┆ 697.46868 ┆ 3964     ┆ 0.9882795 ┆ … ┆ 0.1962728 ┆ 27.792595 ┆ 52.225586 ┆ 10m 33s   │
│           ┆ 67547673  ┆          ┆ 799999677 ┆   ┆ 941127911 ┆ 493319343 ┆ 67676003  ┆ 747161µs  │
│           ┆           ┆          ┆           ┆   ┆ 4         ┆           ┆           ┆           │
│ polygon_z ┆ 135.54231 ┆ 3820     ┆ 0.6000028 ┆ … ┆ 0.4837708 ┆ 32.883479 ┆ 54.293794 ┆ 10m 58s   │
│ kevm      ┆ 376253432 ┆          ┆ 920000006 ┆   ┆ 722700196 ┆ 95462066  ┆ 186959936 ┆ 837391µs  │
└───────────┴───────────┴──────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [ ]:
rollup_cost_stats.with_columns(
    (pl.col("sequencer_calldata_size_mean_kb") / pl.col("base_fee_per_gas_mean")).alias(
        "calldata_size_kb_per_gas"
    ),  # ! does this metric make sense?
    (
        pl.col("sequencer_calldata_size_mean_kb") * pl.col("base_gas_premium_mean_pct")
    ).alias("calldata_size_kb_per_gas_premium"),
    (
        pl.col("sequencer_calldata_size_mean_kb") / pl.col("posts_block_number_mean")
    ).alias("avg_calldata_size_kb_per_block"),
).select(
    "sequencer_names",
    # "post_tx_time_mean",
    "sequencer_calldata_size_mean_kb",
    "posts_block_number_mean",
    "base_fee_per_gas_mean",
    "base_gas_premium_mean_pct",
    "avg_calldata_size_kb_per_block",
    # "calldata_size_kb_per_gas",
    # "calldata_size_kb_per_gas_premium",
)

# Data from 12-10-23 to 1-8-24

shape: (8, 6)
┌────────────────┬────────────────┬────────────────┬───────────────┬───────────────┬───────────────┐
│ sequencer_name ┆ sequencer_call ┆ posts_block_nu ┆ base_fee_per_ ┆ base_gas_prem ┆ avg_calldata_ │
│ s              ┆ data_size_mean ┆ mber_mean      ┆ gas_mean      ┆ ium_mean_pct  ┆ size_kb_per_b │
│ ---            ┆ _kb            ┆ ---            ┆ ---           ┆ ---           ┆ lock          │
│ str            ┆ ---            ┆ f64            ┆ f64           ┆ f64           ┆ ---           │
│                ┆ f64            ┆                ┆               ┆               ┆ f64           │
╞════════════════╪════════════════╪════════════════╪═══════════════╪═══════════════╪═══════════════╡
│ linea          ┆ 148.2875393063 ┆ 1.742609187655 ┆ 32.8598718595 ┆ 0.28015747237 ┆ 85.0951207860 │
│                ┆ 9712           ┆ 492            ┆ 15486         ┆ 520006        ┆ 3424          │
│ arbitrum       ┆ 196.0046481864 ┆ 4.019764967505 ┆ 39.3587687258 ┆ 0.87614792189 ┆ 48.7602259761 │
│                ┆ 8777           ┆ 7034           ┆ 3072          ┆ 8643          ┆ 2473          │
│ optimism       ┆ 229.3959084584 ┆ 8.175311730446 ┆ 33.0397298587 ┆ 0.50885553071 ┆ 28.0595916121 │
│                ┆ 123            ┆                ┆ 0466          ┆ 38645         ┆ 5957          │
│ scroll         ┆ 206.1467211449 ┆ 9.660602982593 ┆ 29.9142499297 ┆ 0.34438304527 ┆ 21.3389082975 │
│                ┆ 6912           ┆ 842            ┆ 07925         ┆ 408636        ┆ 8738          │
│ starknet       ┆ 36.04984678589 ┆ 2.356630622934 ┆ 32.1608383203 ┆ 0.47198696284 ┆ 15.2971986509 │
│                ┆ 252            ┆ 6043           ┆ 04585         ┆ 825004        ┆ 28712         │
│ base           ┆ 74.85507137925 ┆ 4.992119047619 ┆ 32.4592576584 ┆ 0.41618166726 ┆ 14.9946486983 │
│                ┆ 26             ┆ 048            ┆ 0359          ┆ 28986         ┆ 22639         │
│ mantle         ┆ 249.3137184661 ┆ 52.22558667676 ┆ 27.7925954933 ┆ 0.19627289411 ┆ 4.77378492671 │
│                ┆ 8762           ┆ 003            ┆ 19343         ┆ 279114        ┆ 1608          │
│ polygon_zkevm  ┆ 157.0688198952 ┆ 54.29379418695 ┆ 32.8834799546 ┆ 0.48377087227 ┆ 2.89294241169 │
│                ┆ 881            ┆ 9936           ┆ 2066          ┆ 00196         ┆ 48574         │
└────────────────┴────────────────┴────────────────┴───────────────┴───────────────┴───────────────┘

Algorithm: 
*  `posts_block_number_mean` is the average number of blocks a rollup posts data. 
* `avg_calldata_size_kb_per_block` is the average callddata in kb posted per block.

Given preconfirmations as a general future, we can calculate the optimal cost by 

### Charts

In [ ]:
# TITLE - Gas usage per Sequencer. This chart shows the individual gas usage for each sequencer in a block
(
    explore_df.group_by("block_number", "sequencer_names").agg(
        (pl.col("gas_used").sum() / pl.col("gas_used_block").first()).alias(
            "sequencer_gas_used_pct"
        ),
        (pl.col("gas_used_block").first()).alias("total_gas_in_block"),
    )
).sort(by="sequencer_gas_used_pct", descending=True).plot.scatter(
    x="sequencer_gas_used_pct",
    y="total_gas_in_block",
    by="sequencer_names",
    height=600,
    width=800,
    xlabel="Sequencer Gas % Used of Total Block Size",  # Custom X-axis label
    ylabel="Block Size (in millions of Gas)",  # Custom Y-axis label
    title="Gas Usage Per Sequencer",
)

:NdOverlay   [sequencer_names]
   :Scatter   [sequencer_gas_used_pct]   (total_gas_in_block)

In [ ]:
# TITLE - KDE of Total Sequencer Gas Usage
(
    explore_df.group_by("block_number").agg(
        (pl.col("gas_used").sum()).alias("sequencer_gas_used_sum"),
        (pl.col("gas_used_block").first()).alias("total_gas_in_block"),
    )
).sort(by="sequencer_gas_used_sum", descending=True).select(
    "sequencer_gas_used_sum"
).plot.kde(
    title="Collective Gas Usage Per Sequencer",
)

:Distribution   [sequencer_gas_used_sum]   (Density)

In [ ]:
# TITLE - KDE of Total Sequencer Gas Usage
(
    explore_df.group_by("block_number").agg(
        (pl.col("gas_used").sum() / pl.col("gas_used_block").first()).alias(
            "sequencer_gas_used_pct"
        ),
        (pl.col("gas_used_block").first()).alias("total_gas_in_block"),
    )
).sort(by="sequencer_gas_used_pct", descending=True).select(
    "sequencer_gas_used_pct"
).plot.kde(
    title="Collective Gas Usage Per Sequencer",
)

:Distribution   [sequencer_gas_used_pct]   (Density)

In [ ]:
# TITLE - Total Sequencer Gas Usage Over Time
(
    explore_df.group_by("block_number").agg(
        (pl.col("gas_used").sum() / pl.col("gas_used_block").first()).alias(
            "sequencer_gas_used_pct"
        ),
        (pl.col("gas_used_block").first()).alias("total_gas_in_block"),
    )
).sort(by="block_number", descending=True).plot.line(
    x="block_number",
    y="sequencer_gas_used_pct",
    title="Collective Gas Usage Per Sequencer (%)",
)

:Curve   [block_number]   (sequencer_gas_used_pct)

In [ ]:
# TITLE - Total Sequencer Gas Usage Over Time
(
    explore_df.group_by("block_number").agg(
        (pl.col("gas_used").sum()).alias("sequencer_gas_used_sum"),
        (pl.col("gas_used_block").first()).alias("total_gas_in_block"),
    )
).sort(by="block_number", descending=True).plot.line(
    x="block_number",
    y=["sequencer_gas_used_sum"],
    title="Collective Gas Usage Per Sequencer (Gas)",
)

:Curve   [block_number]   (sequencer_gas_used_sum)